## Preambule

In [1]:
# General packages
import numpy as np
import pandas as pd
from tqdm import tqdm
from pathlib import Path
import xarray as xr
import json

# Plotting
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.colors import n_colors

## Parameter

In [2]:
params = dict(start_year_analysis=2021)

In [3]:
rules = ['GF', 'PC', 'PCC', 'AP', 'GDR', 'ECPC']
rulecolors = ['sienna', 'goldenrod', 'forestgreen', 'mediumvioletred', 'steelblue', 'tomato', 'silver']
costoptimal_colors = ['gold', 'orange', 'orangered', 'red', 'darkred']

## Paths

In [4]:
path_main = Path("X:/user/dekkerm/Projects/ECEMF_T5.2/")
path_data = Path("K:/ECEMF/T5.2/")
path_figs = path_main / "Figures" / "ECEMF_paper"

## Read data files

In [5]:
xr_dataread = xr.open_dataset(path_data / "xr_dataread.nc")

all_regions_iso = np.load(path_data / "all_regions.npy")
all_regions_names = np.load(path_data / "all_regions_names.npy")
all_countries_iso = np.load(path_data / "all_countries.npy", allow_pickle=True)
all_countries_names = np.load(path_data / "all_countries_names.npy", allow_pickle=True)

In [6]:
df = pd.read_excel(Path("X:/user/dekkerm/Data/") / "UNFCCC_Parties_Groups_noeu.xlsx", sheet_name = "Country groups")
countries_iso2 = np.array(df["Country ISO Code"])
group_ldc = countries_iso2[np.array(df["LDC"]) == 1]
group_hdc = countries_iso2[np.array(df["HICO"]) == 1]

In [7]:
df = pd.read_excel("X:/user/dekkerm/Data/UNFCCC_Parties_Groups_noeu.xlsx", sheet_name = "Country groups")
countries_iso = np.array(df["Country ISO Code"])
group_cvf = countries_iso[np.array(df["CVF (24/10/22)"]) == 1]
group_g20 = countries_iso[np.array(df["G20"]) == 1]
group_eu = countries_iso[np.array(df["EU"]) == 1]
group_g7 = countries_iso[np.array(df["G7"]) == 1]
group_na = countries_iso[np.array(df["Northern America"]) == 1]
group_um = countries_iso[np.array(df["Umbrella"]) == 1]
group_au = countries_iso[np.array(df["Australasia"]) == 1]
group_af = countries_iso[np.array(df["African Group"]) == 1]
group_sids = countries_iso[np.array(df["SIDS"]) == 1]
group_ldc = countries_iso[np.array(df["LDC"]) == 1]
group_eg = countries_iso[np.array(df["European Group"]) == 1]

XR allocs

In [8]:
# xr_allocs = {}
# for cty in ['EU', 'USA', 'IND', 'CHN', 'JPN', 'AUS', 'BRA', 'RUS', 'ZAF']:
#     xr_allocs[cty] = xr.open_dataset("K:/ECEMF/T5.2/Allocations/" + "xr_alloc_"+cty+".nc")

In [9]:
traj_15 = xr.open_dataset(path_data / "xr_traj_15_50.nc")
xr_alloc_2030 = xr.open_dataset(path_data / "xr_alloc_2030.nc")

2030 alloc Berg

In [10]:
df_berg = pd.read_excel(Path("X:/user/dekkerm/Data/") / "Berg_paper" / "Berg2019_data.xlsx", sheet_name = "Emission pathways")
df_berg2 = df_berg[(df_berg.Scenario == 'Gt400') & (df_berg.Category == 'Emissions|Kyoto Gases') & (df_berg.Year == 2030)].drop(columns=['Scenario', 'Fixed variable', 'Category', 'Year', 'Unnamed: 10',  'Unnamed: 12', 'Region #'])
df_berg2 = df_berg2.rename({'Sensitivity case': "Parameters"}, axis=1)
approaches = np.array(df_berg2.Approach)
approaches[approaches == 'IEPC'] = 'PC'
df_berg2['Approach'] = approaches
df_berg2 = df_berg2.melt(id_vars=["Approach", "Region", "Parameters"], var_name="Range", value_name="Value")
df_berg2 = df_berg2.set_index(['Approach', "Region", "Parameters", "Range"])
xr_berg = df_berg2.to_xarray()

Yann

In [11]:
df_rob = pd.read_excel(Path("X:/user/dekkerm/Data/") / "Robiou_paper" / "Robiou2016_15data.xlsx", sheet_name = "1.5°C National allocations")
df_rob2 = df_rob.drop(columns=['Country names', 'INDC Low assessment', 'INDC average assessment', 'INDC High assessment', 2025, '2025.1', 2030, '2030.1', 2040, '2040.1', 2050, '2050.1', 'Peaking year', 'First net-zero allocation year', 'Budget 2010-2050'])
df_rob2 = df_rob2.rename({'Country code ISO Alpha-3': 'Region', "approaches names": "Approach", 'Budget 2010-2100': "Budget_2010"}, axis=1)
approaches = np.array(df_rob2.Approach)
approaches[approaches == 'CER'] = 'GF'
approaches[approaches == 'EPC'] = 'PCC'
approaches[approaches == 'CAP'] = 'AP'
approaches[approaches == 'CPC'] = 'ECPC'
df_rob2['Approach'] = approaches
df_rob2 = df_rob2.set_index(['Approach', 'Region'])
xr_rob = df_rob2.to_xarray()

Find out high/medium/low income

In [12]:
group_mdc = []
for reg in all_countries_iso:
    if reg not in group_hdc and reg not in group_ldc:
        group_mdc.append(reg)

## Plot

In [13]:
lw = 4
risk = 0.50

In [14]:
# cols_ctys = []
# for cty_i, cty in tqdm(enumerate(all_countries_iso)):
#     try:
#         medians = []
#         xrt = traj_15.sel(Region=cty, Time=2030)
#         for rule in rules[:-1]:
#             # al = np.array(xr_alloc.sel(Region='USA', Time=np.arange(params['start_year_analysis'], 2101)).sum(dim='Time')[rule]).flatten()
#             # al[al == 0] = np.nan
#             vals = xrt[rule]
#             vals = np.array(vals).flatten()
#             vals[vals == 0] = np.nan
#             medians.append(np.nanmedian(vals))
#             # medians.append(float(xr_alloc.sel(Region=cty,
#             #                                      Time=np.arange(params['start_year_analysis'], 2101),
#             #                                      Convergence_year=2070,
#             #                                      Temperature='1.5 deg',
#             #                                      Scenario='SSP2', 
#             #                                      Risk_of_exceedance=0.5,
#             #                                      Non_CO2_mitigation_potential=0.5,
#             #                                      Negative_emissions=0.5)[rule].sum(dim='Time')))
#         idx = np.argmax(medians)
#     except KeyError:
#         idx = -1
#     cols_ctys.append(rulecolors[idx])

In [15]:
cols_ctys2 = []
for cty_i, cty in enumerate(all_countries_iso):
    medians = np.array([traj_15.sel(Time=2040, Convergence_year=2050, Region=cty).median()[i] for i in rules])
    idx = np.argmax(medians)
    cols_ctys2.append(rulecolors[idx])

Traces for panel (a)

In [16]:
traces_panel_a = []

# Cost-optimal
for temp_i, temp in enumerate([1.5, 1.7, 2.0, 2.3]):
       traces_panel_a.append(go.Scatter(x=np.arange(params['start_year_analysis'], 2101),
                                   y=xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Temperature=temp, Risk=risk).GHG_globe.min(dim=['NegEmis', 'NonCO2red', 'Timing'])/1e3,
                                   name="Cost-optimal: "+str(temp)+"&deg;C (50%)",
                                   line={'color': costoptimal_colors[temp_i], 'width': lw/2},
                                   mode='lines',
                                   fill=None,
                                   showlegend=False))
       traces_panel_a.append(go.Scatter(x=np.arange(params['start_year_analysis'], 2101),
                                   y=xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Temperature=temp, Risk=risk).GHG_globe.max(dim=['NegEmis', 'NonCO2red', 'Timing'])/1e3,
                                   name="Cost-optimal: "+str(temp)+"&deg;C (50%)",
                                   line={'color': costoptimal_colors[temp_i], 'width': lw/2},
                                   mode='lines',
                                   fill='tonexty',
                                   showlegend=True))
traces_panel_a.append(go.Scatter(x=np.arange(1990, 2101),
                            y=[0]*len(np.arange(1990, 2101)),
                            line={'color': 'silver', 'width': lw/2, 'dash': 'dash'},
                            mode='lines',
                            showlegend=False))

# Historical emissions
traces_panel_a.append(go.Scatter(x=np.arange(1990, params['start_year_analysis']+1),
                     y=xr_dataread.sel(Time=np.arange(1990, params['start_year_analysis']+1), Region='EARTH').GHG_hist/1e3,
                     name='Historical emissions',
                     line={'color': 'silver', 'width': lw},
                     mode='lines',
                     showlegend=True))
# Baseline emissions
traces_panel_a.append(go.Scatter(x=np.arange(params['start_year_analysis'], 2101),
                            y=xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=countries_iso, Temperature=1.5).GHG_base.sum('Region').min(dim=['Scenario'])/1e3,
                            name='SSP-baselines',
                            fill=None,
                            line={'color': 'grey', 'width': lw/4},
                            mode='lines',
                            showlegend=False))
traces_panel_a.append(go.Scatter(x=np.arange(params['start_year_analysis'], 2101),
                            y=xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=countries_iso, Temperature=1.5).GHG_base.sum('Region').max(dim=['Scenario'])/1e3,
                            name='SSP-baselines',
                            line={'color': 'grey', 'width': lw/4},
                            mode='lines',
                            fill='tonexty',
                            showlegend=True))

traces_panel_a.append(go.Scatter(x=['NDC'],
                     y=[xr_dataread.GHG_ndc.sel(Region=countries_iso).sum(dim='Region').sel(Time=2030).max()/1e3],
                     name='NDCs',
                     line={'color': 'black', 'width': lw},
                     mode='lines+markers',
                     marker={'size': 11, 'symbol': 'triangle-down'},
                     showlegend=False))
traces_panel_a.append(go.Scatter(x=['NDC'],
                     y=[xr_dataread.GHG_ndc.sel(Region=countries_iso).sum(dim='Region').sel(Time=2030).min()/1e3],
                     name='NDCs',
                     line={'color': 'black', 'width': lw},
                     mode='lines+markers',
                     marker={'size': 11, 'symbol': 'triangle-up'},
                     showlegend=False))
traces_panel_a.append(go.Scatter(x=['NDC', 'NDC'],
                     y=[xr_dataread.GHG_ndc.sel(Region=countries_iso).sum(dim='Region').sel(Time=2030).min()/1e3,
                     xr_dataread.GHG_ndc.sel(Region=countries_iso).sum(dim='Region').sel(Time=2030).max()/1e3],
                     name='NDCs',
                     line={'color': 'black', 'width': lw},
                     mode='lines',
                     marker={'size': 11, 'symbol': 'triangle-up'},
                     showlegend=False))

Traces for panel (b)

In [17]:
traces_panel_b = []
for cty_i, cty in enumerate(all_countries_iso):
    pop = float(xr_dataread.Population.sel(Scenario='SSP2', Region=cty, Time=params['start_year_analysis']))
    if not np.isnan(pop):
        if pop > 1e-1:
            popn = np.sqrt(pop / np.nanmax(xr_dataread.Population.sel(Scenario='SSP2', Region=all_countries_iso, Time=params['start_year_analysis'])))
            traces_panel_b.append(go.Scatter(x=[xr_dataread.GDP.sel(Scenario='SSP2', Region=cty, Time=params['start_year_analysis'])*1e9/pop/1e6],
                                    y=[xr_dataread.GHG_hist.sel(Time=np.arange(1950, params['start_year_analysis']), Region=cty).sum(dim='Time')/pop/1e6*1e3],
                                    mode='markers+text',
                                    text=cty,
                                    textfont={'size': popn * 32+3, 'color': 'black'},
                                    marker={'size': popn * 60+8, 'color': cols_ctys2[cty_i], 'opacity': 0.7},
                                    showlegend=False))

Traces for panels (c)-(h)

In [18]:
traces_panels_ch = []
for cty_i, cty in enumerate(['USA', 'EU', 'IND', 'CHN', 'ZAF', 'BRA']):
    traces_panel_i = []
    # Historical emissions
    traces_panel_i.append(go.Scatter(x=np.arange(1990, params['start_year_analysis']+1),
                            y=xr_dataread.sel(Time=np.arange(1990, params['start_year_analysis']+1), Region=cty).GHG_hist/1e3,
                            name='Historical emissions',
                            line={'color': 'silver', 'width': lw},
                            mode='lines',
                            showlegend=False))
    # Baseline emissions
    traces_panel_i.append(go.Scatter(x=np.arange(params['start_year_analysis'], 2101),
                                y=xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty, Temperature=1.5).GHG_base.min(dim='Scenario')/1e3,
                                name='SSP-baselines',
                                fill=None,
                                line={'color': 'grey', 'width': lw/4},
                                mode='lines',
                                showlegend=False))
    traces_panel_i.append(go.Scatter(x=np.arange(params['start_year_analysis'], 2101),
                                y=xr_dataread.sel(Time=np.arange(params['start_year_analysis'], 2101), Region=cty, Temperature=1.5).GHG_base.max(dim='Scenario')/1e3,
                                name='SSP-baselines',
                                line={'color': 'grey', 'width': lw/4},
                                mode='lines',
                                fill='tonexty',
                                showlegend=False))
    for var_i, var in enumerate(rules):
            pars = ['NegEmis', 'NonCO2red', 'Timing']
            if var == 'PCC':
                pars.append('Convergence_year')
                pars.append('Scenario')
            if var == 'PC' or var == 'AP' or var == 'GDR' or var == 'ECPC':
                pars.append("Scenario")
            traces_panel_i.append(go.Scatter(x=np.arange(params['start_year_analysis'], 2101),
                                    y=traj_15.sel(Region=cty)[var].min(dim=pars)/1e3,
                                    name=['Grandfathering', 'Per capita', 'Per capita convergence', 'Ability to pay', 'Greenhouse Development Rights', 'Equal Cumulative per capita'][var_i],
                                    line={'color': rulecolors[var_i], 'width': lw/2},
                                    mode='lines',
                                    fill=None,
                                    showlegend=False))
            traces_panel_i.append(go.Scatter(x=np.arange(params['start_year_analysis'], 2101),
                                    y=traj_15.sel(Region=cty)[var].max(dim=pars)/1e3,
                                    name=['Grandfathering', 'Per capita', 'Per capita convergence', 'Ability to pay', 'Greenhouse Development Rights', 'Equal Cumulative per capita'][var_i],
                                    line={'color': rulecolors[var_i], 'width': lw/2},
                                    mode='lines',
                                    fill='tonexty',
                                    showlegend=[True, False, False, False, False, False][cty_i]))
       
    traces_panel_i.append(go.Scatter(x=[2030],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).max()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines+markers',
                            marker={'size': 11, 'symbol': 'triangle-down'},
                            showlegend=False))
    traces_panel_i.append(go.Scatter(x=[2030],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).min()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines+markers',
                            marker={'size': 11, 'symbol': 'triangle-up'},
                            showlegend=False))
    traces_panel_i.append(go.Scatter(x=[2030, 2030],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).min()/1e3,
                            xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).max()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines',
                            marker={'size': 11, 'symbol': 'triangle-up'},
                            showlegend=False))

    # Violins / 2030 allocations
    traces_panel_j = []
    traces_panel_j.append(go.Scatter(x=['NDC'],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).max()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines+markers',
                            marker={'size': 11, 'symbol': 'triangle-down'},
                            showlegend=False))
    traces_panel_j.append(go.Scatter(x=['NDC'],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).min()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines+markers',
                            marker={'size': 11, 'symbol': 'triangle-up'},
                            showlegend=False))
    traces_panel_j.append(go.Scatter(x=['NDC', 'NDC'],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).min()/1e3,
                            xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).max()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines',
                            marker={'size': 11, 'symbol': 'triangle-up'},
                            showlegend=False))
        
    for rule_i, rule in enumerate(rules):
        vals = np.array(xr_alloc_2030.sel(Region=cty, Temperature=1.5, Risk=risk)[rule]).flatten()
        vals[vals == 0] = np.nan
        vals20 = np.array(xr_alloc_2030.sel(Region=cty, Temperature=1.7, Risk=risk)[rule]).flatten()
        vals20[vals20 == 0] = np.nan
        vals25 = np.array(xr_alloc_2030.sel(Region=cty, Temperature=2.0, Risk=risk)[rule]).flatten()
        vals25[vals25 == 0] = np.nan
        vals30 = np.array(xr_alloc_2030.sel(Region=cty, Temperature=2.3, Risk=risk)[rule]).flatten()
        vals30[vals30 == 0] = np.nan
        # traces_panel_j.append(go.Violin(x=[rule]*len(vals),
        #                         y=vals30/1e3,
        #                         side='negative',
        #                         showlegend=False,
        #                         points=False,
        #                         opacity=0.1,
        #                         line_color=rulecolors[rule_i])
        #             )
        # traces_panel_j.append(go.Violin(x=[rule]*len(vals),
        #                         y=vals30/1e3,
        #                         side='positive',
        #                         showlegend=False,
        #                         points=False,
        #                         opacity=0.1,
        #                         line_color=rulecolors[rule_i])
        #             )
        # traces_panel_j.append(go.Violin(x=[rule]*len(vals),
        #                         y=vals25/1e3,
        #                         side='negative',
        #                         showlegend=False,
        #                         points=False,
        #                         opacity=0.3,
        #                         line_color=rulecolors[rule_i])
        #             )
        # traces_panel_j.append(go.Violin(x=[rule]*len(vals),
        #                         y=vals25/1e3,
        #                         side='positive',
        #                         showlegend=False,
        #                         points=False,
        #                         opacity=0.3,
        #                         line_color=rulecolors[rule_i])
        #             )
        # traces_panel_j.append(go.Violin(x=[rule]*len(vals),
        #                         y=vals20/1e3,
        #                         side='negative',
        #                         showlegend=False,
        #                         points=False,
        #                         opacity=0.5,
        #                         line_color=rulecolors[rule_i])
        #             )
        # traces_panel_j.append(go.Violin(x=[rule]*len(vals),
        #                         y=vals20/1e3,
        #                         side='positive',
        #                         showlegend=False,
        #                         points=False,
        #                         opacity=0.5,
        #                         line_color=rulecolors[rule_i])
        #             )
        traces_panel_j.append(go.Violin(x=[rule]*len(vals),
                                y=vals/1e3,
                                side='negative',
                                showlegend=False,
                                points=False,
                                line={'width': 4},
                                line_color=rulecolors[rule_i])
                    )
        traces_panel_j.append(go.Violin(x=[rule]*len(vals),
                                y=vals/1e3,
                                side='positive',
                                showlegend=False,
                                points=False,
                                line={'width': 4},
                                line_color=rulecolors[rule_i])
                    )
        try:
            vals_berg = np.array(xr_berg.sel(Region=cty, Approach=rule).Value*3.67).flatten()
            vals_berg[vals_berg == 0] = np.nan
            traces_panel_j.append(go.Box(x=[rule]*len(vals),
                                    y=vals_berg,
                                    showlegend=False,
                                    line_color=rulecolors[rule_i])
                        )
        except KeyError:
            3
        if cty_i == 1: cty = 'EU'

    for rule_i, rule in enumerate(rules):
        vals = np.array(xr_alloc_2030.sel(Region=cty, Temperature=1.5, Risk=risk)[rule]).flatten()
        vals[vals == 0] = np.nan
        traces_panel_j.append(go.Scatter(x=['NDC']+list(rules[:rule_i+1]),
                                y=[np.nanmedian(vals)/1e3]*(len(rules[:rule_i+1])+1),
                                line={'color': rulecolors[rule_i], 'width': 1, 'dash': 'dot'},
                                mode='lines',
                                showlegend=False)
                    )

    for rule_i, rule in enumerate(rules):
        vals = np.array(xr_alloc_2030.sel(Region=cty, Temperature=1.5, Risk=risk)[rule]).flatten()
        vals[vals == 0] = np.nan
        traces_panel_j.append(go.Scatter(x=['NDC'],
                                y=[np.nanmedian(vals)/1e3],
                                marker={'color': rulecolors[rule_i], 'size': 10},
                                mode='markers',
                                showlegend=False)
                    )
    traces_panel_j.append(go.Scatter(x=['NDC'],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).max()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines+markers',
                            marker={'size': 11, 'symbol': 'triangle-down'},
                            showlegend=False))
    traces_panel_j.append(go.Scatter(x=['NDC'],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).min()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines+markers',
                            marker={'size': 11, 'symbol': 'triangle-up'},
                            showlegend=False))
    traces_panel_j.append(go.Scatter(x=['NDC', 'NDC'],
                            y=[xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).min()/1e3,
                            xr_dataread.GHG_ndc.sel(Region=cty).sel(Time=2030).max()/1e3],
                            name='NDCs',
                            line={'color': 'black', 'width': lw},
                            mode='lines',
                            marker={'size': 11, 'symbol': 'triangle-up'},
                            showlegend=False))
    traces_panels_ch.append([traces_panel_i, traces_panel_j])

Full plot

In [19]:
df_ar6_raw = pd.read_csv("X:/user/dekkerm/Data/IPCC/AR6_Scenarios_Database_World_v1.1.csv")
df_ar6 = df_ar6_raw[df_ar6_raw.Variable.isin(['Emissions|Kyoto Gases'])]
df_ar6 = df_ar6.reset_index(drop=True)
  
df_ar6_meta = pd.read_excel("X:/user/dekkerm/Data/IPCC/AR6_Scenarios_Database_metadata_indicators_v1.1.xlsx", sheet_name='meta_Ch3vetted_withclimate')
mods = np.array(df_ar6_meta.Model)
scens = np.array(df_ar6_meta.Scenario)
modscens_meta = np.array([mods[i]+'|'+scens[i] for i in range(len(scens))])
df_ar6_meta['ModelScenario'] = modscens_meta
df_ar6_meta = df_ar6_meta[['ModelScenario', 'Category', 'Policy_category']]
df_ar6_meta = df_ar6_meta[df_ar6_meta.Category.isin(['C1', 'C2'])]
df_ar6_meta = df_ar6_meta.reset_index(drop=True)
ms_meta_refined = np.array(df_ar6_meta.ModelScenario)

mods = np.array(df_ar6.Model)
scens = np.array(df_ar6.Scenario)
modscens = np.array([mods[i]+'|'+scens[i] for i in range(len(scens))])
df_ar6['ModelScenario'] = modscens
df_ar6 = df_ar6.drop(['Model', 'Scenario', 'Unit', 'Region'], axis=1)
df_ar6_c1 = df_ar6[df_ar6.ModelScenario.isin(np.array(ms_meta_refined))]

In [20]:
dummy = df_ar6_c1.melt(id_vars=["Variable", "ModelScenario"], var_name="Time", value_name="Value")
dummy['Time'] = np.array(dummy['Time'].astype(int))
dummy = dummy.set_index(["Variable", "ModelScenario", "Time"])
xr_scen = xr.Dataset.from_dataframe(dummy)
xr_scen = xr_scen.reindex(Time = np.arange(1990, 2101))
xr_scen_c1 = xr_scen.interpolate_na(dim="Time", method="linear")

startpoint = xr_dataread.sel(Time=2021, Region="EARTH").GHG_hist
kyoto2021 = xr_scen_c1.sel(Time=2021)/1e3
offsets = (startpoint/1e3-kyoto2021)
ar6_corr = xr_scen_c1.sel(Time=np.arange(2021, 2101))/1e3 + offsets

compensation_form = np.array([1]*80)#np.array(list(np.linspace(0, 1, len(np.arange(2021, 2050))))+[1]*len(np.arange(2050, 2101)))
ms = ar6_corr.ModelScenario[np.where(np.abs(ar6_corr.sel(Variable='Emissions|Kyoto Gases', Time=np.arange(2021, 2101)).sum(dim='Time').Value*1e3 - float(xr_dataread.GHG_globe.sel(NegEmis=0.5, NonCO2red=0.5, Timing='Immediate', Temperature=1.5, Risk=0.5, Time=np.arange(2021, 2101)).sum(dim='Time'))) < 75000)[0]]

ar6_filtered = ar6_corr.sel(ModelScenario=ms)

In [21]:
fig = make_subplots(rows=4, cols=6,
                    specs=[[{'colspan': 4, 'rowspan': 2}, {}, {}, {}, {'colspan': 2, 'rowspan': 2}, {}],
                           [{}, {}, {}, {}, {}, {}],
                           [{}, {}, {}, {}, {}, {}],
                           [{}, {}, {}, {}, {}, {}]],
                    horizontal_spacing = 0.03, vertical_spacing=0.06)

# Panel (a)
# for ms_i, ms in enumerate(ar6_filtered.ModelScenario):
#      fig.add_trace(go.Scatter(x = ar6_filtered.Time.sel(Time=np.arange(2021, 2101)), y = ar6_filtered.sel(Variable='Emissions|Kyoto Gases', Time=np.arange(2021, 2101), ModelScenario=ms).Value, line={'color': 'black', 'width': 0.8}, showlegend=False), 1, 1)
for t_i, t in enumerate(traces_panel_a):
     fig.add_trace(t, 1, 1)

# Panel (b)
for t_i, t in enumerate(traces_panel_b):
     fig.add_trace(t, 1, 5)

# Panel (c)-(h)
for a_i, a in enumerate(traces_panels_ch):
     for b_i, traces in enumerate(a):
          for t_i, t in enumerate(traces):
               fig.add_trace(t, [3, 4][b_i], [1, 2, 3, 4, 5, 6][a_i])

fig.update_xaxes(title_text="GDP per capita in 2021 [USD]", type="log", row=1, col=5, range=[2.4, 5])
fig.update_yaxes(type="log", row=1, col=5, range=[-1.8, 0.5])
fig.update_layout(legend=dict(
    yanchor="top",
    y=0.76,
    xanchor="left",
    x=0.01,
    font=dict(
        size=11,
        color="black"
    ),
))
fig.update_yaxes(title_text="Global GHG emissions [Gt CO<sub>2</sub>e/yr]", row=1, col=1)
fig['layout'].update(
    annotations=[dict(x=0.05, y=1.0, text='<b>(a) Global GHG emission trajectories</b>', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=16)),
                 dict(x=0.93, y=1.0, text='<b>(b) Relation to country indicators</b><br>(color indicates 2040 preference)', xref='paper', yref='paper', showarrow=False, font=dict(color='black', size=16)),
                 dict(x=0.71, y=0.92, text='GHG emissions 1950-2021 per capita [kt CO<sub>2</sub>e]', xref='paper', yref='paper', showarrow=False, textangle=-90, font=dict(color='black',  size=16)),
                 dict(x=2040, y=7, text='<b>(c) United States</b>', xref='x13', yref='y13', showarrow=False, font=dict(color='black', size=16)),
                 dict(x=2042, y=5, text='<b>(d) European Union</b>', xref='x14', yref='y14', showarrow=False, font=dict(color='black', size=16)),
                 dict(x=2040, y=11, text='<b>(e) India</b>', xref='x15', yref='y15', showarrow=False, font=dict(color='black', size=16)),
                 dict(x=2055, y=16.5, text='<b>(f) China</b>', xref='x16', yref='y16', showarrow=False, font=dict(color='black', size=16)),
                 dict(x=2040, y=0.8, text='<b>(g) South-Africa</b>', xref='x17', yref='y17', showarrow=False, font=dict(color='black', size=16)),
                 dict(x=2040, y=3.3, text='<b>(h) Brazil</b>', xref='x18', yref='y18', showarrow=False, font=dict(color='black', size=16)),
])
fig.update_yaxes(ticks="inside")
fig.update_xaxes(ticks="inside")
fig.update_yaxes(title_text="GHG emissions allocations<br>[Gt CO<sub>2</sub>e/yr]<br>for reaching 1.5&deg;C (50%)", row=3, col=1)
fig.update_yaxes(title_text="GHG emission allocation<br>in 2030 [Gt CO<sub>2</sub>e]<br>for reaching 1.5&deg;C (50%)", row=4, col=1)
fig.update_layout(height=1300, width=1600, template='simple_white')
fig.show()

In [24]:
fig.write_image("../../FIgures/ECEMF_paper/Figure_1.png", scale=6)

## Preference map

In [23]:
# fig = make_subplots(rows=1, cols=1, 
#                     specs=[[{'type': 'choropleth'}]],
#                     horizontal_spacing = 0.05, vertical_spacing=0.08)

# fig.add_trace(
#     go.Choropleth(
#     locations=regs,
#     z = data,
#     locationmode = 'ISO-3',
#     colorscale = colmap,
#     zmax = 1,
#     zmin = 0,
#     text = [str(r)+": "+str(int(data[r_i]*6))+" out of 6" for r_i, r in enumerate(regs)],
#     hovertemplate  = '%{text}',
#     name="",
#     marker_line_color='black', 
#     marker_line_width=1.,
#     colorbar=dict(len=0.43, x=0.37, y=0.45, orientation='h',
#                   tickvals = np.arange(0, 1.1, 1/6),
#                   thickness=15,
#                   tickfont={'size': 10},
#                   ticktext=['None<br>(Mitigation financed<br>by others)', '1 out of 6', '2 out of 6', '3 out of 6', '4 out of 6', '5 out of 6', 'All<br>(Finances mitigation<br>abroad)'],
#                   ticklabelposition='outside',
#     ),
#     showscale=True
# ), 1, 1)
# fig.add_trace(
#     go.Choropleth(
#     locations=group_eu,
#     z = [data[np.where(regs == "EU")[0][0]]]*len(group_eu),
#     locationmode = 'ISO-3',
#     colorscale = colmap,
#     zmax = 1,
#     zmin = 0,
#     text = ["EU: "+str(int(6*data[regs == 'EU']))+" out of 6"for r_i, r in enumerate(group_eu)],
#     hovertemplate  = '%{text}',
#     name="",
#     marker_line_color='black', 
#     marker_line_width=1.,
#     showscale=False
# ), 1, 1)
# fig.update_geos(showocean=True, oceancolor="aliceblue")
# fig.update_geos(showlakes=True, lakecolor="aliceblue")

# # limite map scope to USA 'africa', 'asia', 'europe', 'north america', 'south america', 'usa', 'world'
# fig.update_geos(visible=True,
#                 showlakes=False,
#                 lakecolor='rgb(255, 255, 255)',
#                 projection_type='natural earth',
#                 showcoastlines=False,)

# # Panel labels
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='left', ay=-0, showarrow=False, font=dict(color='black', size=18),
#                    y=1.04, x=0.20, text="<b>(a) Fair-share allocations less than cost-optimal</b><br>          (in number of effort-sharing approaches)")
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='right', ay=-0, showarrow=False, font=dict(color='black', size=16), y=0.38, x=0.01, text="<b>(b) United States of America")
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='right', ay=-0, showarrow=False, font=dict(color='black', size=16), y=0.38, x=0.27, text="<b>(c) Brazil")
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='right', ay=-0, showarrow=False, font=dict(color='black', size=16), y=0.38, x=0.60, text="<b>(d) South-Africa")
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='right', ay=-0, showarrow=False, font=dict(color='black', size=16), y=1.02, x=0.94, text="<b>(e) European Union")
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='right', ay=-0, showarrow=False, font=dict(color='black', size=16), y=0.81, x=0.87, text="<b>(f) Russia")
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='right', ay=-0, showarrow=False, font=dict(color='black', size=16), y=0.58, x=0.87, text="<b>(g) China")
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='right', ay=-0, showarrow=False, font=dict(color='black', size=16), y=0.38, x=0.87, text="<b>(h) India")
# fig.add_annotation(xref='paper', yref='paper',ax=0, align='left', ay=-0, showarrow=False, font=dict(color='black', size=16), y=0.14, x=0.01, text="<b>(i) Policy costs over 2020-2100 in cost-optimal scenarios</b>")

# # ADD LINES TO PATHS
# fig.update_yaxes(title_text="Full-century GHG emission<br>budget [Gt CO<sub>2</sub>e]", row=4, col=1)
# fig.update_yaxes(title_text="Cumulative consumption<br>loss as fraction<br>of GDP in 2019", row=5, col=1)

# fig.update_yaxes(rangemode="tozero")
# fig.update_xaxes(zeroline=True, zerolinewidth=2, zerolinecolor='Black')
# fig.update_layout(height=1100,
#                   width=1400,
#                   template='simple_white')
# fig.show()